Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [48]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<a id='item1'></a>

## 1. Download and Explore Dataset for NewYork

In [49]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


#### Load and explore the data

Next, let's load the data.

In [50]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)['features']
    


#### Tranform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

In [51]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)


Then let's loop through the data and fill the dataframe one row at a time.

In [52]:
for data in newyork_data:
    print(data['properties']['borough'])
    print(data['properties']['name'])
    borough =data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    print(neighborhood_lon)
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
    
neighborhoods.head()


Bronx
Wakefield
-73.84720052054902
Bronx
Co-op City
-73.82993910812398
Bronx
Eastchester
-73.82780644716412
Bronx
Fieldston
-73.90564259591682
Bronx
Riverdale
-73.9125854610857
Bronx
Kingsbridge
-73.90281798724604
Manhattan
Marble Hill
-73.91065965862981
Bronx
Woodlawn
-73.86731496814176
Bronx
Norwood
-73.8793907395681
Bronx
Williamsbridge
-73.85744642974207
Bronx
Baychester
-73.83579759808117
Bronx
Pelham Parkway
-73.85475564017999
Bronx
City Island
-73.78648845267413
Bronx
Bedford Park
-73.8855121841913
Bronx
University Heights
-73.9104159619131
Bronx
Morris Heights
-73.91967159119565
Bronx
Fordham
-73.89642655981623
Bronx
East Tremont
-73.88735617532338
Bronx
West Farms
-73.87774474910545
Bronx
High  Bridge
-73.9261020935813
Bronx
Melrose
-73.90942160757436
Bronx
Mott Haven
-73.91609987487575
Bronx
Port Morris
-73.91322139386135
Bronx
Longwood
-73.8957882009446
Bronx
Hunts Point
-73.88331505955291
Bronx
Morrisania
-73.90150648943059
Bronx
Soundview
-73.86574609554924
Bronx
Clason Po

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [63]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

Combine Manhattan Data & Toronto Data

In [77]:
response = requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M").text

from bs4 import BeautifulSoup
soup =BeautifulSoup(response,'lxml')
table =soup.tbody
rows = table.findAll('tr')
columns = ['PostCode', 'Borough', 'Neighborhood']
list=[]
df={}
for row in rows[1:]:
    cells = row.findAll('td')
    if (cells[1].text == 'Not assigned'):
     continue  
    postCode= cells[0].text
    borough = cells[1].text
    neigh = cells[2].text.strip()
    if (neigh == 'Not assigned'):
        neigh = borough
    df={
        'PostCode': postCode,
        'Borough' : borough,
        'Neighborhood'   : neigh,
     }
    list.append(df)
    
Neigh= pd.DataFrame(list, columns=columns)
Neigh = Neigh.groupby(['PostCode','Borough'])['Neighborhood'].apply(','.join).reset_index()


es = pd.read_csv('Geospatial_Coordinates.csv')

Neigh = pd.concat([Neigh,es['Latitude'],es['Longitude']],axis=1)
array=['Downtown Toronto','East Toronto', 'Central Toronto', 'West Toronto']
toronto_data = Neigh[Neigh['Borough'].isin(array)].reset_index(drop=True)
toronto_data.head()
    
toronto_data.drop(columns=['PostCode'],inplace=True)
toronto_data.reset_index(drop=True).head()

manhattan_data = manhattan_data.append(toronto_data)

manhattan_data = pd.concat([manhattan_data,toronto_data]).drop_duplicates().reset_index(drop=True)

manhattan_data


Borough                                       Neighborhood  \
0          Manhattan                                        Marble Hill   
1          Manhattan                                          Chinatown   
2          Manhattan                                 Washington Heights   
3          Manhattan                                             Inwood   
4          Manhattan                                   Hamilton Heights   
5          Manhattan                                     Manhattanville   
6          Manhattan                                     Central Harlem   
7          Manhattan                                        East Harlem   
8          Manhattan                                    Upper East Side   
9          Manhattan                                          Yorkville   
10         Manhattan                                         Lenox Hill   
11         Manhattan                                   Roosevelt Island   
12         Manhattan                                    Upper West Side   
13         Manhattan                                     Lincoln Square   
14         Manhattan                                            Clinton   
15         Manhattan                                            Midtown   
16         Manhattan                                        Murray Hill   
17         Manhattan                                            Chelsea   
18         Manhattan                                  Greenwich Village   
19         Manhattan                                       East Village   
20         Manhattan                                    Lower East Side   
21         Manhattan                                            Tribeca   
22         Manhattan                                       Little Italy   
23         Manhattan                                               Soho   
24         Manhattan                                       West Village   
25         Manhattan                                   Manhattan Valley   
26         Manhattan                                Morningside Heights   
27         Manhattan                                           Gramercy   
28         Manhattan                                  Battery Park City   
29         Manhattan                                 Financial District   
30         Manhattan                                      Carnegie Hill   
31         Manhattan                                               Noho   
32         Manhattan                                       Civic Center   
33         Manhattan                                      Midtown South   
34         Manhattan                                       Sutton Place   
35         Manhattan                                         Turtle Bay   
36         Manhattan                                         Tudor City   
37         Manhattan                                    Stuyvesant Town   
38         Manhattan                                           Flatiron   
39         Manhattan                                       Hudson Yards   
40      East Toronto                                        The Beaches   
41      East Toronto                        The Danforth West,Riverdale   
42      East Toronto                      The Beaches West,India Bazaar   
43      East Toronto                                    Studio District   
44   Central Toronto                                      Lawrence Park   
45   Central Toronto                                   Davisville North   
46   Central Toronto                                 North Toronto West   
47   Central Toronto                                         Davisville   
48   Central Toronto                         Moore Park,Summerhill East   
49   Central Toronto  Deer Park,Forest Hill SE,Rathnelly,South Hill,...   
50  Downtown Toronto                                           Rosedale   
51  Downtown Toronto                         Cabbagetown,St. James Town   
52  Downtown Toronto                  

Let's get the geographical coordinates of Manhattan.

In [78]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7900869, -73.9598295.


Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [79]:
CLIENT_ID = 'SQ2NLTOR2MD0LVFHJWQX0L5RPCJMEM4LNY5XJ4JKQLK3ATFD' # your Foursquare ID
CLIENT_SECRET = 'RXSYRHUPAPSRIVQQDPLXVKTEMMOCJW0QFJF1I4ETNTKDOIPO' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: SQ2NLTOR2MD0LVFHJWQX0L5RPCJMEM4LNY5XJ4JKQLK3ATFD
CLIENT_SECRET:RXSYRHUPAPSRIVQQDPLXVKTEMMOCJW0QFJF1I4ETNTKDOIPO


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [80]:
manhattan_data.loc[0, 'Neighborhood']

'Marble Hill'

Get the neighborhood's latitude and longitude values.

In [81]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

print(neighborhood_name)
print(neighborhood_latitude)

Marble Hill
40.87655077879964


#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [82]:
# type your answer here
manhattan_data.head()
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)



Double-click __here__ for the solution.
<!-- The correct answer is:
LIMIT = 100 # limit of number of venues returned by Foursquare API
-->

<!--
radius = 500 # define radius
-->

<!--
\\ # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL
--> 

Send the GET request and examine the resutls

In [83]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5c4f84419fb6b76788c47955'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 24,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b4429abf964a52037f225e3',
       'name': "Arturo's",
       'location': {'address': '5198 Broadway',
        'crossStreet': 'at 225th St.',
        'lat': 40.87441177110231,
        'lng': -73.91027100981574,
        'labeledLatLngs': [{'label'

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [84]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [85]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name          categories        lat        lng
0               Arturo's         Pizza Place  40.874412 -73.910271
1            Bikram Yoga         Yoga Studio  40.876844 -73.906204
2          Tibbett Diner               Diner  40.880404 -73.908937
3              Starbucks         Coffee Shop  40.877531 -73.905582
4  Land & Sea Restaurant  Seafood Restaurant  40.877885 -73.905873

And how many venues were returned by Foursquare?

In [ ]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

<a id='item2'></a>

## 2. Explore Neighborhoods in Manhattan

#### Let's create a function to repeat the same process to all the neighborhoods in Manhattan

In [86]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *manhattan_venues*.

In [87]:
# type your answer here

manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )



Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards
The Beaches
The Danforth West,Riverdale
The Beaches West,India Bazaar
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park,Summerhill East
Deer Park,Forest Hill SE,Rathnelly,South Hill,Summerhill West
Rosedale
Cabbagetown,St. James Town
Church and Wellesley
Harbourfront,Regent Park
Ryerson,Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide,King,Richmond
Harbourfront East,Toronto Islands,Union Station
Design Exchange,Toronto D

Double-click __here__ for the solution.
<!-- The correct answer is:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )
--> 

#### Let's check the size of the resulting dataframe

In [89]:
print(manhattan_venues.shape)
manhattan_venues.head()

(5011, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551               -73.91066   
1  Marble Hill              40.876551               -73.91066   
2  Marble Hill              40.876551               -73.91066   
3  Marble Hill              40.876551               -73.91066   
4  Marble Hill              40.876551               -73.91066   

                   Venue  Venue Latitude  Venue Longitude      Venue Category  
0               Arturo's       40.874412       -73.910271         Pizza Place  
1            Bikram Yoga       40.876844       -73.906204         Yoga Studio  
2          Tibbett Diner       40.880404       -73.908937               Diner  
3              Starbucks       40.877531       -73.905582         Coffee Shop  
4  Land & Sea Restaurant       40.877885       -73.905873  Seafood Restaurant

Let's check how many venues were returned for each neighborhood

In [90]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide,King,Richmond                                                100   
Battery Park City                                                     100   
Berczy Park                                                            56   
Brockton,Exhibition Place,Parkdale Village                             18   
Business Reply Mail Processing Centre 969 Eastern                      16   
CN Tower,Bathurst Quay,Island airport,Harbourfr...                     14   
Cabbagetown,St. James Town                                             47   
Carnegie Hill                                                         100   
Central Bay Street                                                     83   
Central Harlem                                                         44   
Chelsea                                                               100   
Chinatown                                                             100   
Chinatown,Grange Park,Kensington Market                               100   
Christie                                                               16   
Church and Wellesley                                                   86   
Civic Center                                                          100   
Clinton                                                               100   
Commerce Court,Victoria Hotel                                         100   
Davisville                                                             36   
Davisville North                                                        7   
Deer Park,Forest Hill SE,Rathnelly,South Hill,S...                     14   
Design Exchange,Toronto Dominion Centre                               100   
Dovercourt Village,Dufferin                                            20   
East Harlem                                                            47   
East Village                                                          100   
Financial District                                                    100   
First Canadian Place,Underground city                                 100   
Flatiron                                                              100   
Forest Hill North,Forest Hill West                                      4   
Gramercy                                                              100   
Greenwich Village                                                     100   
Hamilton Heights                                                       57   
Harbord,University of Toronto                                          34   
Harbourfront East,Toronto Islands,Union Station                       100   
Harbourfront,Regent Park                                               47   
High Park,The Junction South                                           23   
Hudson Yards                                                           60   
Inwood                                                                 58   
Lawrence Park                                                           4   
Lenox Hill                                                            100   
Lincoln Square                                                        100   
Little Italy                                                          100   
Little Portugal,Trinity                                                65   
Lower East Side                                                        62   
Manhattan Valley                                                       64   
Manhattanville                                                         39   
Marble Hill                                                            24   
Midtown                                                               100   
Midtown South                                                         100   
Moore Park,Summerhill East                                              3   
Morningside Heights                             

#### Let's find out how many unique categories can be curated from all the returned venues

In [91]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 372 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [93]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

manhattan_onehot.head()

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0                  0               0                  0                   0   
1                  0               0                  0                   0   
2                  0               0                  0                   0   
3                  0               0                  0                   0   
4                  0               0                  0                   0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal  American Restaurant  Animal Shelter  Antique Shop  \
0                 0                    0               0             0   
1                 0                    0               0             0   
2                 0                    0               0             0   
3                 0                    0               0             0   
4                 0                    0               0             0   

   Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0         0       0                 0                       0            0   
1         0       0                 0                       0            0   
2         0       0                 0                       0            0   
3         0       0                 0                       0            0   
4         0       0                 0                       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auditorium  Australian Restaurant  Austrian Restaurant  Auto Workshop  \
0           0                      0                    0              0   
1           0                      0                    0              0   
2           0                      0                    0              0   
3           0                      0                    0              0   
4           0                      0                    0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0    

And let's examine the new dataframe size.

In [94]:
manhattan_onehot.shape

(5011, 372)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [120]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  \
0                              Adelaide,King,Richmond           0.000000   
1                                   Battery Park City           0.000000   
2                                         Berczy Park           0.000000   
3          Brockton,Exhibition Place,Parkdale Village           0.000000   
4   Business Reply Mail Processing Centre 969 Eastern           0.000000   
5   CN Tower,Bathurst Quay,Island airport,Harbourf...           0.000000   
6                          Cabbagetown,St. James Town           0.000000   
7                                       Carnegie Hill           0.000000   
8                                  Central Bay Street           0.000000   
9                                      Central Harlem           0.000000   
10                                            Chelsea           0.000000   
11                                          Chinatown           0.000000   
12            Chinatown,Grange Park,Kensington Market           0.000000   
13                                           Christie           0.000000   
14                               Church and Wellesley           0.000000   
15                                       Civic Center           0.000000   
16                                            Clinton           0.000000   
17                      Commerce Court,Victoria Hotel           0.000000   
18                                         Davisville           0.000000   
19                                   Davisville North           0.000000   
20  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
21            Design Exchange,Toronto Dominion Centre           0.000000   
22                        Dovercourt Village,Dufferin           0.000000   
23                                        East Harlem           0.000000   
24                                       East Village           0.000000   
25                                 Financial District           0.010000   
26              First Canadian Place,Underground city           0.000000   
27                                           Flatiron           0.000000   
28                 Forest Hill North,Forest Hill West           0.000000   
29                                           Gramercy           0.000000   
30                                  Greenwich Village           0.000000   
31                                   Hamilton Heights           0.000000   
32                      Harbord,University of Toronto           0.000000   
33    Harbourfront East,Toronto Islands,Union Station           0.000000   
34                           Harbourfront,Regent Park           0.000000   
35                       High Park,The Junction South           0.000000   
36                                       Hudson Yards           0.000000   
37                                             Inwood           0.000000   
38                                      Lawrence Park           0.000000   
39                                         Lenox Hill           0.000000   
40                                     Lincoln Square           0.000000   
41                                       Little Italy           0.000000   
42                            Little Portugal,Trinity           0.000000   
43                                    Lower East Side           0.000000   
44                                   Manhattan Valley           0.000000   
45                                     Manhattanville           0.000000   
46                                        Marble Hill           0.000000   
47                                            Midtown           0.000000   
48                                      Midtown South           0.000000   
49                         Moore Park,Summerhill East           0.000000   
50                                Morningside Heights           0.000000   
51                                        Murray Hill           0.000000   
52           

#### Let's confirm the new size

In [ ]:
manhattan_grouped.shape

#### Let's print each neighborhood along with the top 5 most common venues

In [104]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    print(temp)
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    print(temp)
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(1))
    print('\n')

----Adelaide,King,Richmond----
                                        index                       0
0                                Neighborhood  Adelaide,King,Richmond
1                           Accessories Store                       0
2                              Adult Boutique                       0
3                           Afghan Restaurant                       0
4                          African Restaurant                       0
5                                     Airport                       0
6                          Airport Food Court                       0
7                                Airport Gate                       0
8                              Airport Lounge                       0
9                             Airport Service                       0
10                           Airport Terminal                       0
11                        American Restaurant                    0.04
12                             Animal Shelter              

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [107]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [108]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                             Adelaide,King,Richmond           Coffee Shop   
1                                  Battery Park City           Coffee Shop   
2                                        Berczy Park           Coffee Shop   
3         Brockton,Exhibition Place,Parkdale Village                  Café   
4  Business Reply Mail Processing Centre 969 Eastern    Light Rail Station   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café       Thai Restaurant            Steakhouse   
1                  Park                 Hotel             Wine Shop   
2            Restaurant          Cocktail Bar           Cheese Shop   
3        Breakfast Spot           Coffee Shop               Stadium   
4           Yoga Studio         Auto Workshop         Garden Center   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0   American Restaurant        Clothing Store                   Gym   
1    Italian Restaurant          Cupcake Shop         Shopping Mall   
2            Steakhouse              Beer Bar        Farmers Market   
3         Burrito Place                   Bar         Grocery Store   
4                Garden  Fast Food Restaurant        Farmers Market   

  8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
0            Restaurant                 Bakery                  Hotel  
1          Burger Joint          Women's Store         Ice Cream Shop  
2                  Café                 Bakery     Seafood Restaurant  
3                   Gym  Performing Arts Venue           Climbing Gym  
4                  Park            Pizza Place             Comic Shop

<a id='item4'></a>

In [109]:
manhattan_grouped

Neighborhood  Accessories Store  \
0                              Adelaide,King,Richmond           0.000000   
1                                   Battery Park City           0.000000   
2                                         Berczy Park           0.000000   
3          Brockton,Exhibition Place,Parkdale Village           0.000000   
4   Business Reply Mail Processing Centre 969 Eastern           0.000000   
5   CN Tower,Bathurst Quay,Island airport,Harbourf...           0.000000   
6                          Cabbagetown,St. James Town           0.000000   
7                                       Carnegie Hill           0.000000   
8                                  Central Bay Street           0.000000   
9                                      Central Harlem           0.000000   
10                                            Chelsea           0.000000   
11                                          Chinatown           0.000000   
12            Chinatown,Grange Park,Kensington Market           0.000000   
13                                           Christie           0.000000   
14                               Church and Wellesley           0.000000   
15                                       Civic Center           0.000000   
16                                            Clinton           0.000000   
17                      Commerce Court,Victoria Hotel           0.000000   
18                                         Davisville           0.000000   
19                                   Davisville North           0.000000   
20  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
21            Design Exchange,Toronto Dominion Centre           0.000000   
22                        Dovercourt Village,Dufferin           0.000000   
23                                        East Harlem           0.000000   
24                                       East Village           0.000000   
25                                 Financial District           0.010000   
26              First Canadian Place,Underground city           0.000000   
27                                           Flatiron           0.000000   
28                 Forest Hill North,Forest Hill West           0.000000   
29                                           Gramercy           0.000000   
30                                  Greenwich Village           0.000000   
31                                   Hamilton Heights           0.000000   
32                      Harbord,University of Toronto           0.000000   
33    Harbourfront East,Toronto Islands,Union Station           0.000000   
34                           Harbourfront,Regent Park           0.000000   
35                       High Park,The Junction South           0.000000   
36                                       Hudson Yards           0.000000   
37                                             Inwood           0.000000   
38                                      Lawrence Park           0.000000   
39                                         Lenox Hill           0.000000   
40                                     Lincoln Square           0.000000   
41                                       Little Italy           0.000000   
42                            Little Portugal,Trinity           0.000000   
43                                    Lower East Side           0.000000   
44                                   Manhattan Valley           0.000000   
45                                     Manhattanville           0.000000   
46                                        Marble Hill           0.000000   
47                                            Midtown           0.000000   
48                                      Midtown South           0.000000   
49                         Moore Park,Summerhill East           0.000000   
50                                Morningside Heights           0.000000   
51                                        Murray Hill           0.000000   
52           

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [129]:
# set number of clusters
kclusters = 5

print(type(manhattan_grouped))

manhattan_grouped_clustering = manhattan_grouped.drop(['Neighborhood'], 1).reset_index()
print(type(manhattan_grouped_clustering))

#print(manhattan_grouped_clustering)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:100] 

<class 'pandas.core.frame.DataFrame'>
<class 'pandas.core.frame.DataFrame'>


array([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [130]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               3   
1  Manhattan           Chinatown  40.715618 -73.994279               2   
2  Manhattan  Washington Heights  40.851903 -73.936900               1   
3  Manhattan              Inwood  40.867684 -73.921210               0   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Discount Store           Coffee Shop           Yoga Studio   
1    Chinese Restaurant       Bubble Tea Shop    Dim Sum Restaurant   
2                  Café     Mobile Phone Shop                Bakery   
3                  Café    Mexican Restaurant           Pizza Place   
4    Mexican Restaurant                  Café           Coffee Shop   

  4th Most Common Venue  5th Most Common Venue 6th Most Common Venue  \
0         Deli / Bodega             Steakhouse       Supplement Shop   
1   American Restaurant  Vietnamese Restaurant          Cocktail Bar   
2        Sandwich Place            Pizza Place         Deli / Bodega   
3                Lounge                   Park   American Restaurant   
4         Deli / Bodega            Pizza Place     Indian Restaurant   

  7th Most Common Venue      8th Most Common Venue 9th Most Common Venue  \
0         Shopping Mall                 Shoe Store            Donut Shop   
1     Hotpot Restaurant         Salon / Barbershop                Bakery   
2    Mexican Restaurant  Latin American Restaurant            Donut Shop   
3    Chinese Restaurant                 Restaurant              Pharmacy   
4          Liquor Store               Cocktail Bar                School   

  10th Most Common Venue  
0     Seafood Restaurant  
1           Noodle House  
2       Tapas Restaurant  
3          Deli / Bodega  
4   Caribbean Restaurant

Finally, let's visualize the resulting clusters

In [131]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [ ]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

#### Cluster 2

In [ ]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

#### Cluster 3

In [ ]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

#### Cluster 4

In [ ]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

#### Cluster 5

In [ ]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]